In [1]:
from Evaluation.find_ranking_citation import CitationRanking
from sklearn.metrics.pairwise import linear_kernel,cosine_similarity
from Evaluation.write_result import WriteResult
from data_loading_ginny import DataLoading
from Evaluation.mean_reciprocal_ranking import MRR
from  Evaluation.eval_Ginny import Metrics
from Rec_configuraiton import Rec_configuration 
#from reranking.re_ranking_title import ReRankingTitle
#advanced deep learning stuff
import torch
#from bert_serving.client import BertClient
import pickle
from collections import defaultdict
import numpy as np
import scipy
#from sentence_transformers import SentenceTransformer
#from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
import os 
from scipy.spatial.distance import cdist

In [2]:
#import tensorflow as tf
import tensorflow_hub as hub
import numpy as np

In [3]:
!ls resources/

all_associated_article.pickle  final_pmids_abstract.pickle  tf_idf_models
article			       geo_csv_files.txt	    use
bert_raw		       geo_dataset.pickle	    use4Maybe
BM25			       inferSent		    word2vec
dataset			       lsa			    word2vec_models
doc2vec			       README.txt
elmo			       short_forms.txt


In [3]:
#download the model to local so it can be used again and again
#!mkdir sentence_wise_email/module/module_useT
# Download the module, and uncompress it to the destination folder. 
!curl -L "https://tfhub.dev/google/elmo/3?tf-hub-format=compressed" | tar -zxvC resources/elmo

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
./
./saved_model.pb
./variables/
./variables/variables.data-00000-of-00001
100  331M  100  331M    0     0  51.4M      0  0:00:06  0:00:06 --:--:-- 56.6M
./variables/variables.index
./tfhub_module.pb


In [4]:
import tensorflow.compat.v1 as tf
#To make tf 2.0 compatible with tf1.0 code, we disable the tf2.0 functionalities
tf.disable_eager_execution()

In [5]:

embed = hub.Module("resources/elmo")

# Compute a representation for each message, showing various lengths supported.
word = "Elephant"
sentence = "I am a sentence for which I would like to get its embedding."
paragraph = (
    "Universal Sentence Encoder embeddings also support short paragraphs. "
    "There is no hard limit on how long the paragraph is. Roughly, the longer "
    "the more 'diluted' the embedding will be.")
messages = [word, sentence, paragraph]

# Reduce logging output.
tf.logging.set_verbosity(tf.logging.ERROR)

with tf.Session() as session:
    session.run([tf.global_variables_initializer(), tf.tables_initializer()])
    message_embeddings = session.run(embed(messages))

    for i, message_embedding in enumerate(np.array(message_embeddings).tolist()):
        print("Message: {}".format(messages[i]))
        print("Embedding size: {}".format(len(message_embedding)))
        message_embedding_snippet = ", ".join((str(x) for x in message_embedding[:3]))
        print("Embedding: [{}, ...]\n".format(message_embedding_snippet))

Message: Elephant
Embedding size: 1024
Embedding: [0.06389404833316803, -0.12069519609212875, -0.19782808423042297, ...]

Message: I am a sentence for which I would like to get its embedding.
Embedding size: 1024
Embedding: [-0.48454535007476807, -0.3442211449146271, 0.06355403363704681, ...]

Message: Universal Sentence Encoder embeddings also support short paragraphs. There is no hard limit on how long the paragraph is. Roughly, the longer the more 'diluted' the embedding will be.
Embedding size: 1024
Embedding: [0.1125347837805748, 0.5053393840789795, -0.4854649603366852, ...]



In [6]:
import tensorflow_hub as hub
def embed_useT(module):
    with tf.Graph().as_default():
        sentences = tf.placeholder(tf.string)
        embed = hub.Module(module)
        embeddings = embed(sentences)
        session = tf.train.MonitoredSession()
    return lambda x: session.run(embeddings, {sentences: x})

embed_fn = embed_useT('resources/elmo')

In [7]:
messages = [
    "we are sorry for the inconvenience",
    "we are sorry for the delay",
    "we regret for your inconvenience",
    "we don't deliver to baner region in pune",
    "we will get you the best possible rate"
]

In [8]:
encoding_matrix = embed_fn(messages)
#np.inner(encoding_matrix[0], encoding_matrix)
cdist([encoding_matrix[0]], encoding_matrix, "cosine")[0]

array([2.22044605e-16, 4.11937441e-02, 1.51704928e-01, 4.81842049e-01,
       5.01571354e-01])

In [9]:
cosine_similarity([encoding_matrix[0]], encoding_matrix) #seems like this is the berst 

array([[1.0000001 , 0.95880634, 0.84829515, 0.51815814, 0.49842873]],
      dtype=float32)

In [10]:
type(encoding_matrix)

numpy.ndarray

In [12]:
class Master:
    def __init__(self, rerank = True):
        self.rec_conf = Rec_configuration()
        self.article_title, self.article_abstract, self.geo_title, \
        self.geo_summary, self.citation_data = DataLoading().get_all_details() #we should get actual citations
        self.auto_rank = CitationRanking(self.citation_data)
        self.write_res = WriteResult()
     
        '''
        #later we're gonna test on all datasets that has referenced paper 
        self.geo_test_data = ["GSE20361", "GSE23137", "GSE1640", "GSE41034", "GSE1864", "GSE44700", "GSE50988"]#, \
                              #"GSE46045", "GSE32869", "GSE22955", "GSE41072", "GSE50624", "GSE18684", "GSE770", \
                              #"GSE9048", "GSE9854", "GSE23135", "GSE23136", "GSE23139", "GSE49583", "GSE49584", \
                              #"GSE49586", "GSE64073", "GSE38623", "GSE3113", "GSE41491", "GSE29641", "GSE26002", \
                              #"GSE17018", "GSE71121", "GSE21618", "GSE23138", "GSE20988", "GSE52710", "GSE14103", \
                              #"GSE53294"] #36
        '''
        #or,
        choose = list(self.citation_data.keys())
        self.geo_test_data = [key for key in choose if self.citation_data[key] != []] #76,064
        #self.rr = ReRankingTitle() # i definitely need to work on this as well (re-ranking title using bert)
        self.top_threshold = 10 #sounds nice
        self.rerank = rerank
        #USE
        self.model_addr = self.rec_conf.model_path_elmo #subject to change
        self.model = embed_useT('resources/elmo')
        self.res_addr = self.rec_conf.result_address_elmo #subject to change
    
    def process(self):
        #check paths and check vecs        
        pmids, elmo_vecs = None, None #this should be loading something

        # This is for loading the pre-trained bert models.
        if elmo_vecs is not None and pmids is not None:
            print('load trained models and encoded publications vectors')
            '''
            
            '''
        else:
            print('Building models')
            joined_dict_article = {}
            for pmid in self.article_title: #for articles, encoding the articles
                #print('pmid')
                #print(pmid)
                if (self.article_title[pmid] + self.article_abstract[pmid]).strip() != '':
                    joined_dict_article[pmid] = self.article_title[pmid] + ' ' + self.article_abstract[pmid]
            #should be some training here, otherwise just do the easiest encodinh
            #pmids, use_vecs = list(joined_dict_article.keys()), self.model(list(joined_dict_article.values()))
            #use_vecs = np.array(use_vecs).tolist()
            with open(self.res_addr + 'smallbase/joined_dict_article', 'wb') as handle:
                pickle.dump(joined_dict_article, handle, protocol=pickle.HIGHEST_PROTOCOL)
            #with open(self.res_addr + 'smallbase/pmids', 'wb') as handle:
                #pickle.dump(pmids, handle, protocol=pickle.HIGHEST_PROTOCOL)
        
        #keep only articles with non-zero values
        #new_article_abstract = {new_key: self.article_abstract[new_key] for new_key in pmids} #770,525
        #new_article_title = {new_key: self.article_title[new_key] for new_key in pmids}
   
    
        joined_dict_geo = {} # maxium: 76,064
        # screening first for those geo_ids with pmids 
        for geo_id in self.geo_test_data:
            print('geo_id')
            print(geo_id)
            if (self.geo_title[geo_id] + self.geo_summary[geo_id]).strip() != '':
                #only get the ones with actual texts
                joined_dict_geo[geo_id] = self.geo_title[geo_id] + ' ' + self.geo_summary[geo_id]
        #geo_ids, geo_use_vecs = list(joined_dict_geo.keys()), self.model(list(joined_dict_geo.values()))
        #geo_use_vecs = np.array(geo_use_vecs).tolist()
        with open(self.res_addr + 'smallbase/joined_dict_geo', 'wb') as handle:
            pickle.dump(joined_dict_geo, handle, protocol=pickle.HIGHEST_PROTOCOL)
        #with open(self.res_addr + 'smallbase/geo_ids', 'wb') as handle:
            #pickle.dump(geo_ids, handle, protocol=pickle.HIGHEST_PROTOCOL)        


In [13]:
def main():
    x = Master(rerank = False)
    x.process()


if __name__ == '__main__':
    main()

Loading all geo related preprocessed datasets
Loaded all geo related processed datasets
Loading all title and abstract
Loaded all title and abstract
Building models
geo_id
GSE103837
geo_id
GSE89809
geo_id
GSE11663
geo_id
GSE55127
geo_id
GSE61914
geo_id
GSE96174
geo_id
GSE108140
geo_id
GSE55064
geo_id
GSE77553
geo_id
GSE836
geo_id
GSE48997
geo_id
GSE4248
geo_id
GSE71695
geo_id
GSE16495
geo_id
GSE92231
geo_id
GSE36779
geo_id
GSE28180
geo_id
GSE97290
geo_id
GSE76313
geo_id
GSE27104
geo_id
GSE78579
geo_id
GSE33842
geo_id
GSE96211
geo_id
GSE27139
geo_id
GSE25518
geo_id
GSE72425
geo_id
GSE96905
geo_id
GSE8547
geo_id
GSE12256
geo_id
GSE76217
geo_id
GSE43669
geo_id
GSE10903
geo_id
GSE105628
geo_id
GSE72212
geo_id
GSE44657
geo_id
GSE92332
geo_id
GSE81888
geo_id
GSE4500
geo_id
GSE83148
geo_id
GSE32214
geo_id
GSE70328
geo_id
GSE81569
geo_id
GSE55869
geo_id
GSE65781
geo_id
GSE37546
geo_id
GSE89581
geo_id
GSE101478
geo_id
GSE1862
geo_id
GSE43906
geo_id
GSE24450
geo_id
GSE3574
geo_id
GSE1865
geo_id


geo_id
GSE41902
geo_id
GSE43721
geo_id
GSE59021
geo_id
GSE62389
geo_id
GSE83586
geo_id
GSE38863
geo_id
GSE23888
geo_id
GSE46398
geo_id
GSE86897
geo_id
GSE51553
geo_id
GSE1515
geo_id
GSE27289
geo_id
GSE81519
geo_id
GSE21653
geo_id
GSE12243
geo_id
GSE54097
geo_id
GSE26646
geo_id
GSE83407
geo_id
GSE82428
geo_id
GSE102859
geo_id
GSE33507
geo_id
GSE12887
geo_id
GSE5208
geo_id
GSE94041
geo_id
GSE32120
geo_id
GSE70865
geo_id
GSE94883
geo_id
GSE64912
geo_id
GSE76114
geo_id
GSE78089
geo_id
GSE55143
geo_id
GSE40259
geo_id
GSE47224
geo_id
GSE68359
geo_id
GSE22324
geo_id
GSE96396
geo_id
GSE34578
geo_id
GSE105822
geo_id
GSE46300
geo_id
GSE55347
geo_id
GSE32356
geo_id
GSE42199
geo_id
GSE43965
geo_id
GSE97847
geo_id
GSE40341
geo_id
GSE2151
geo_id
GSE31429
geo_id
GSE96150
geo_id
GSE99403
geo_id
GSE20210
geo_id
GSE6596
geo_id
GSE99466
geo_id
GSE12912
geo_id
GSE13978
geo_id
GSE20563
geo_id
GSE68984
geo_id
GSE65176
geo_id
GSE47379
geo_id
GSE98772
geo_id
GSE86597
geo_id
GSE84012
geo_id
GSE76178
geo_id
GSE

geo_id
GSE72335
geo_id
GSE5057
geo_id
GSE98903
geo_id
GSE15505
geo_id
GSE95183
geo_id
GSE10959
geo_id
GSE10505
geo_id
GSE65386
geo_id
GSE103004
geo_id
GSE99508
geo_id
GSE80840
geo_id
GSE92492
geo_id
GSE23247
geo_id
GSE2127
geo_id
GSE105601
geo_id
GSE30387
geo_id
GSE56276
geo_id
GSE48258
geo_id
GSE36167
geo_id
GSE78577
geo_id
GSE77564
geo_id
GSE45786
geo_id
GSE57915
geo_id
GSE71367
geo_id
GSE61605
geo_id
GSE27585
geo_id
GSE51346
geo_id
GSE16683
geo_id
GSE93799
geo_id
GSE76841
geo_id
GSE33908
geo_id
GSE54655
geo_id
GSE82744
geo_id
GSE31105
geo_id
GSE49114
geo_id
GSE14043
geo_id
GSE48475
geo_id
GSE25829
geo_id
GSE86414
geo_id
GSE75775
geo_id
GSE12078
geo_id
GSE7687
geo_id
GSE13044
geo_id
GSE65640
geo_id
GSE74818
geo_id
GSE4315
geo_id
GSE40623
geo_id
GSE10622
geo_id
GSE65273
geo_id
GSE19612
geo_id
GSE92909
geo_id
GSE54158
geo_id
GSE17706
geo_id
GSE82305
geo_id
GSE20675
geo_id
GSE32086
geo_id
GSE26387
geo_id
GSE66995
geo_id
GSE3218
geo_id
GSE69897
geo_id
GSE66891
geo_id
GSE74061
geo_id
GSE9

GSE15256
geo_id
GSE78491
geo_id
GSE46955
geo_id
GSE44855
geo_id
GSE90421
geo_id
GSE54766
geo_id
GSE78428
geo_id
GSE88327
geo_id
GSE41178
geo_id
GSE35655
geo_id
GSE104039
geo_id
GSE77533
geo_id
GSE19619
geo_id
GSE31871
geo_id
GSE71891
geo_id
GSE81900
geo_id
GSE76254
geo_id
GSE29211
geo_id
GSE91737
geo_id
GSE89748
geo_id
GSE2497
geo_id
GSE66753
geo_id
GSE13288
geo_id
GSE42657
geo_id
GSE54364
geo_id
GSE72196
geo_id
GSE74817
geo_id
GSE9300
geo_id
GSE76962
geo_id
GSE81774
geo_id
GSE43780
geo_id
GSE41405
geo_id
GSE75953
geo_id
GSE74525
geo_id
GSE3298
geo_id
GSE59507
geo_id
GSE27326
geo_id
GSE3700
geo_id
GSE37959
geo_id
GSE96364
geo_id
GSE64179
geo_id
GSE96683
geo_id
GSE54419
geo_id
GSE80990
geo_id
GSE3611
geo_id
GSE23260
geo_id
GSE11384
geo_id
GSE64520
geo_id
GSE31077
geo_id
GSE72056
geo_id
GSE97679
geo_id
GSE78176
geo_id
GSE41797
geo_id
GSE58451
geo_id
GSE51791
geo_id
GSE87747
geo_id
GSE72986
geo_id
GSE96307
geo_id
GSE93625
geo_id
GSE73745
geo_id
GSE16051
geo_id
GSE47863
geo_id
GSE53995
geo

GSE92061
geo_id
GSE75511
geo_id
GSE14533
geo_id
GSE4447
geo_id
GSE4971
geo_id
GSE82333
geo_id
GSE90664
geo_id
GSE91755
geo_id
GSE59422
geo_id
GSE5894
geo_id
GSE36470
geo_id
GSE105252
geo_id
GSE93133
geo_id
GSE44022
geo_id
GSE61265
geo_id
GSE20205
geo_id
GSE67816
geo_id
GSE41548
geo_id
GSE13255
geo_id
GSE23388
geo_id
GSE63405
geo_id
GSE61434
geo_id
GSE53495
geo_id
GSE26055
geo_id
GSE90417
geo_id
GSE4531
geo_id
GSE41833
geo_id
GSE62000
geo_id
GSE66827
geo_id
GSE91226
geo_id
GSE104708
geo_id
GSE53215
geo_id
GSE31066
geo_id
GSE96813
geo_id
GSE31170
geo_id
GSE11258
geo_id
GSE66219
geo_id
GSE11043
geo_id
GSE26441
geo_id
GSE21053
geo_id
GSE34716
geo_id
GSE6495
geo_id
GSE87025
geo_id
GSE10197
geo_id
GSE75907
geo_id
GSE32881
geo_id
GSE16628
geo_id
GSE72241
geo_id
GSE28385
geo_id
GSE21176
geo_id
GSE99067
geo_id
GSE92871
geo_id
GSE60631
geo_id
GSE49643
geo_id
GSE60495
geo_id
GSE63596
geo_id
GSE51564
geo_id
GSE34234
geo_id
GSE52664
geo_id
GSE15606
geo_id
GSE100851
geo_id
GSE22317
geo_id
GSE22991
g

...

GSE45159
geo_id
GSE41079
geo_id
GSE42173
geo_id
GSE80872
geo_id
GSE66310
geo_id
GSE13783
geo_id
GSE36873
geo_id
GSE65350
geo_id
GSE33050
geo_id
GSE42097
geo_id
GSE66660
geo_id
GSE63249
geo_id
GSE28982
geo_id
GSE8651
geo_id
GSE39875
geo_id
GSE92558
geo_id
GSE12210
geo_id
GSE72273
geo_id
GSE13548
geo_id
GSE95415
geo_id
GSE30540
geo_id
GSE105814
geo_id
GSE34098
geo_id
GSE39542
geo_id
GSE12660
geo_id
GSE9560
geo_id
GSE18737
geo_id
GSE55053
geo_id
GSE82926
geo_id
GSE6541
geo_id
GSE11923
geo_id
GSE38382
geo_id
GSE5666
geo_id
GSE92820
geo_id
GSE88105
geo_id
GSE15568
geo_id
GSE36099
geo_id
GSE59613
geo_id
GSE58131
geo_id
GSE62493
geo_id
GSE82543
geo_id
GSE10570
geo_id
GSE47442
geo_id
GSE56450
geo_id
GSE83422
geo_id
GSE64491
geo_id
GSE53030
geo_id
GSE82165
geo_id
GSE92910
geo_id
GSE29498
geo_id
GSE18618
geo_id
GSE74810
geo_id
GSE62156
geo_id
GSE53069
geo_id
GSE68514
geo_id
GSE28158
geo_id
GSE54363
geo_id
GSE94304
geo_id
GSE15789
geo_id
GSE8909
geo_id
GSE88065
geo_id
GSE72323
geo_id
GSE25628
geo

GSE77549
geo_id
GSE12244
geo_id
GSE21490
geo_id
GSE19358
geo_id
GSE99701
geo_id
GSE96427
geo_id
GSE92911
geo_id
GSE63766
geo_id
GSE100920
geo_id
GSE58804
geo_id
GSE35021
geo_id
GSE77603
geo_id
GSE91073
geo_id
GSE83798
geo_id
GSE38253
geo_id
GSE5185
geo_id
GSE84767
geo_id
GSE6331
geo_id
GSE25279
geo_id
GSE5189
geo_id
GSE32142
geo_id
GSE71545
geo_id
GSE54038
geo_id
GSE62520
geo_id
GSE29100
geo_id
GSE47992
geo_id
GSE88966
geo_id
GSE67688
geo_id
GSE7487
geo_id
GSE11249
geo_id
GSE98985
geo_id
GSE15765
geo_id
GSE27885
geo_id
GSE100086
geo_id
GSE37912
geo_id
GSE7713
geo_id
GSE17048
geo_id
GSE62851
geo_id
GSE8830
geo_id
GSE52866
geo_id
GSE65217
geo_id
GSE24530
geo_id
GSE100992
geo_id
GSE91069
geo_id
GSE91256
geo_id
GSE15931
geo_id
GSE2655
geo_id
GSE10804
geo_id
GSE96682
geo_id
GSE49334
geo_id
GSE82787
geo_id
GSE99014
geo_id
GSE23391
geo_id
GSE71847
geo_id
GSE80568
geo_id
GSE7281
geo_id
GSE51264
geo_id
GSE107205
geo_id
GSE67442
geo_id
GSE69695
geo_id
GSE11688
geo_id
GSE30126
geo_id
GSE34596
geo

geo_id
GSE89567
geo_id
GSE89616
geo_id
GSE7620
geo_id
GSE8157
geo_id
GSE107454
geo_id
GSE51509
geo_id
GSE26419
geo_id
GSE29646
geo_id
GSE82604
geo_id
GSE33489
geo_id
GSE26813
geo_id
GSE79127
geo_id
GSE107292
geo_id
GSE55031
geo_id
GSE12786
geo_id
GSE31784
geo_id
GSE24472
geo_id
GSE2211
geo_id
GSE86443
geo_id
GSE44104
geo_id
GSE12945
geo_id
GSE24237
geo_id
GSE45558
geo_id
GSE857
geo_id
GSE99998
geo_id
GSE81810
geo_id
GSE71512
geo_id
GSE99343
geo_id
GSE1772
geo_id
GSE13790
geo_id
GSE82881
geo_id
GSE9102
geo_id
GSE3576
geo_id
GSE42853
geo_id
GSE53049
geo_id
GSE60372
geo_id
GSE73976
geo_id
GSE2419
geo_id
GSE59896
geo_id
GSE19582
geo_id
GSE52701
geo_id
GSE59846
geo_id
GSE19473
geo_id
GSE28380
geo_id
GSE35158
geo_id
GSE43378
geo_id
GSE89604
geo_id
GSE3915
geo_id
GSE94115
geo_id
GSE38511
geo_id
GSE6364
geo_id
GSE1375
geo_id
GSE15850
geo_id
GSE95662
geo_id
GSE51438
geo_id
GSE677
geo_id
GSE39498
geo_id
GSE32321
geo_id
GSE85615
geo_id
GSE51503
geo_id
GSE66497
geo_id
GSE44824
geo_id
GSE55488
geo_

geo_id
GSE24839
geo_id
GSE105849
geo_id
GSE60364
geo_id
GSE9589
geo_id
GSE27240
geo_id
GSE95591
geo_id
GSE75369
geo_id
GSE906
geo_id
GSE31648
geo_id
GSE72934
geo_id
GSE21659
geo_id
GSE22269
geo_id
GSE91909
geo_id
GSE22720
geo_id
GSE75368
geo_id
GSE83311
geo_id
GSE11386
geo_id
GSE61848
geo_id
GSE7326
geo_id
GSE43912
geo_id
GSE55974
geo_id
GSE37233
geo_id
GSE2816
geo_id
GSE30073
geo_id
GSE75982
geo_id
GSE82685
geo_id
GSE88620
geo_id
GSE50395
geo_id
GSE36586
geo_id
GSE87102
geo_id
GSE90321
geo_id
GSE80875
geo_id
GSE40246
geo_id
GSE34001
geo_id
GSE68197
geo_id
GSE97487
geo_id
GSE38631
geo_id
GSE9135
geo_id
GSE93816
geo_id
GSE54314
geo_id
GSE64553
geo_id
GSE30258
geo_id
GSE36667
geo_id
GSE77705
geo_id
GSE74001
geo_id
GSE81737
geo_id
GSE5474
geo_id
GSE20493
geo_id
GSE95899
geo_id
GSE3202
geo_id
GSE21741
geo_id
GSE26140
geo_id
GSE36792
geo_id
GSE79166
geo_id
GSE48154
geo_id
GSE59051
geo_id
GSE69280
geo_id
GSE51616
geo_id
GSE73160
geo_id
GSE46150
geo_id
GSE69104
geo_id
GSE65360
geo_id
GSE42527

GSE57718
geo_id
GSE51134
geo_id
GSE581
geo_id
GSE22767
geo_id
GSE54568
geo_id
GSE28895
geo_id
GSE28876
geo_id
GSE62617
geo_id
GSE71725
geo_id
GSE78963
geo_id
GSE27381
geo_id
GSE31022
geo_id
GSE82478
geo_id
GSE51628
geo_id
GSE54034


In [11]:
#read-in stored vec 
res_addr = 'results/elmo_plain/smallbase/'
#res_addr2 = 'results/bert_plain/'
with open(res_addr +'joined_dict_article', 'rb') as fp:
      joined_dict_article = pickle.load(fp)
with open(res_addr +'joined_dict_geo', 'rb') as fp:
      joined_dict_geo = pickle.load(fp)        
"""
with open(res_addr +'pmids', 'rb') as fp:
      pmids = pickle.load(fp)
with open(res_addr +'geo_ids', 'rb') as fp:
      geo_ids = pickle.load(fp)


"""

"\nwith open(res_addr +'pmids', 'rb') as fp:\n      pmids = pickle.load(fp)\nwith open(res_addr +'geo_ids', 'rb') as fp:\n      geo_ids = pickle.load(fp)\n\n\n"

In [12]:
pmids = list(joined_dict_article.keys() )
geo_ids = list(joined_dict_geo.keys() )

In [13]:
elmo = list(joined_dict_article.values())


In [14]:
geo_elmo = list(joined_dict_geo.values())

In [22]:
b_size =128
chunks = len(elmo) // b_size +1
for step in range(chunks):
    batch = elmo[step*b_size:(step+1)*b_size]
    batch = embed_fn(batch)
    np.save(res_addr + 'elmo_vecs_batch' + str(step), batch )

In [12]:
step = 391

In [13]:
elmo_vecs = np.load(res_addr + 'elmo_vecs_batch0.npy')
#print
#for file in files:
for i in range(1, step +1):
    batch = np.load(res_addr + 'elmo_vecs_batch' + str(i) + '.npy')
    elmo_vecs = np.concatenate((elmo_vecs,batch), axis = 0)

In [14]:
with open(res_addr + 'elmo_vecs', 'wb') as handle:
    pickle.dump(elmo_vecs, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [15]:
with open(res_addr +'elmo_vecs', 'rb') as fp:
      elmo_vecs = pickle.load(fp) 

In [16]:
elmo_vecs.shape

(50159, 1024)

In [17]:
len(elmo_vecs)

50159

In [18]:
type(elmo_vecs)

numpy.ndarray

In [19]:
elmo_vecs[1]

array([ 0.2663285 ,  0.5477236 ,  0.1660655 , ...,  0.02443554,
        0.4788341 , -0.01123247], dtype=float32)

In [20]:
def sort_this(geo_sim_dict, pmid_ls, top_threshold =10):

    '''
    for each geo_id, give a list of recommendations 
    this could be for non-reranking or reranking
    '''
    geo_sim_dict = dict(geo_sim_dict)
    similarity_dict = defaultdict()
    sim_np = np.asarray(list(geo_sim_dict.values()))
    idx_np = np.argsort(-sim_np, axis= 1) #so the big values will be in front 
    #take on # of top_threshold
    idx_np = idx_np[:,:top_threshold]
    sim_np_taketop = np.take_along_axis(sim_np, idx_np, axis=1) 
    for i, geo_id in enumerate(geo_sim_dict):
        print('working')
        pmid_selected = list(np.take(pmid_ls, idx_np[i]))
        selected = dict(zip(pmid_selected, sim_np_taketop[i]))
        similarity_dict[geo_id] = selected     
    return similarity_dict

In [21]:
#do numpy only 
from Evaluation.find_ranking_citation import CitationRanking
from Evaluation.write_result import WriteResult
from data_loading_ginny import DataLoading
from Evaluation.mean_reciprocal_ranking import MRR
from Evaluation.eval_Ginny import Metrics      
import os 
_, _, _, _, citation_data = DataLoading().get_all_details() #we should get actual citations
auto_rank = CitationRanking(citation_data)
write_res = WriteResult()  
b_size = 64
#use_vecs = np.array(use_vecs)

Loading all geo related preprocessed datasets
Loaded all geo related processed datasets
Loading all title and abstract
Loaded all title and abstract


In [22]:
#numpy only
#device  = torch.device("cuda" if torch.cuda.is_available() else "cpu")
#this = [1,2,3,4,5,6,7]
chunks = len(geo_elmo) // b_size +1
for step in range(chunks):
    batch = geo_elmo[step*b_size:(step+1)*b_size]
    batch = embed_fn(batch)
    #batch = np.array(batch)
    print(batch.shape)
    geo_ids_batch = geo_ids[step*b_size: (step+1)*b_size]
    #geo_batch, geo_ids_batch = batch
    similarity_value_dict = dict()
    similarity_scores = cosine_similarity(batch, elmo_vecs)
    np.save(res_addr + 'similarity_scores_batch_' + str(step), similarity_scores)#.cpu().numpy())
    print(similarity_scores.shape)
    #call the re-ranking or not 
    for i, geo_id in enumerate(geo_ids_batch): #this is only from testing geo_id
        print(geo_id)
        similarity_value_dict[geo_id] =  list(similarity_scores[i])#.cpu().numpy())
        #similarity_value_dict[geo_id] = scipy.spatial.distance.cdist([geo_bert_vecs[i]], bert_vecs, "cosine")[0]
        '''
        if self.rerank:
        new_similarity_dict = self.re_rank_bert(geo_sim_dict = similarity_value_dict,
                                                   article_title = new_article_title,
                                                   geo_title = new_geo_title, 
                                                   pmid_ls = pmids)
        '''

    new_similarity_dict =  sort_this(geo_sim_dict = similarity_value_dict, pmid_ls = pmids)
    new_similarity_dict = dict(new_similarity_dict)
    filename =  res_addr + 'new_similarity_dict_batch_' + str(step)
    os.makedirs(os.path.dirname(filename), exist_ok=True)
    with open(res_addr + 'new_similarity_dict_batch_' + str(step), 'wb') as handle:
        pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)   
    print('export dict!!!!!!!!')
     
        #screen for geo_ids that actually has citations t
    for id, geo_id in enumerate(geo_ids_batch): 
        print(geo_id)
        #this has already stored in a pickled list of geo_haspmid.pickle
        temp_selected = new_similarity_dict[geo_id]
        filename =  res_addr + geo_id + '.txt'
        os.makedirs(os.path.dirname(filename), exist_ok=True)
        write_res.write(res_addr  + geo_id + '.txt', temp_selected)
        auto_rank.find_citations(geo_id, list(temp_selected.keys())) #keys are a list of pmids

a, b, c, d = auto_rank.get_values() #need to modify this 
print('good geo recommendations = {}, top1 hit geo recommendations = {}, bad geo recommendations = {}, '
      'geo without citations = {}'.format(a, b, c, d))
#we need many more than just MRR

(64, 1024)
(64, 50159)
GSE103837
GSE89809
GSE11663
GSE55127
GSE61914
GSE96174
GSE108140
GSE55064
GSE77553
GSE836
GSE48997
GSE4248
GSE71695
GSE16495
GSE92231
GSE36779
GSE28180
GSE97290
GSE76313
GSE27104
GSE78579
GSE33842
GSE96211
GSE27139
GSE25518
GSE72425
GSE96905
GSE8547
GSE12256
GSE76217
GSE43669
GSE10903
GSE105628
GSE72212
GSE44657
GSE92332
GSE81888
GSE4500
GSE83148
GSE32214
GSE70328
GSE81569
GSE55869
GSE65781
GSE37546
GSE89581
GSE101478
GSE1862
GSE43906
GSE24450
GSE3574
GSE1865
GSE101823
GSE32925
GSE84727
GSE62309
GSE70285
GSE64244
GSE83819
GSE35910
GSE61188
GSE86956
GSE51389
GSE42241
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
work

(64, 1024)
(64, 50159)
GSE78738
GSE50803
GSE83435
GSE40738
GSE74446
GSE22962
GSE29617
GSE98976
GSE11133
GSE11347
GSE45430
GSE84122
GSE66178
GSE39375
GSE79901
GSE21120
GSE58318
GSE229
GSE59071
GSE88426
GSE78633
GSE52662
GSE66966
GSE94069
GSE25842
GSE89944
GSE37450
GSE38916
GSE5174
GSE20214
GSE15434
GSE114205
GSE9482
GSE74925
GSE53621
GSE88414
GSE53017
GSE63926
GSE87153
GSE27911
GSE38596
GSE46262
GSE79108
GSE59246
GSE84822
GSE6022
GSE65352
GSE37047
GSE21607
GSE88997
GSE27632
GSE91771
GSE91494
GSE76015
GSE8863
GSE966
GSE105483
GSE66590
GSE26930
GSE13100
GSE17064
GSE78375
GSE46101
GSE90045
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working

(64, 1024)
(64, 50159)
GSE12670
GSE72537
GSE39528
GSE46889
GSE105302
GSE50748
GSE54709
GSE94960
GSE64945
GSE56253
GSE30325
GSE75271
GSE13925
GSE55279
GSE51573
GSE64680
GSE57570
GSE51525
GSE7094
GSE49042
GSE3872
GSE81689
GSE30610
GSE4824
GSE31438
GSE38222
GSE47759
GSE64106
GSE87992
GSE24135
GSE91485
GSE23546
GSE45795
GSE79680
GSE95237
GSE34721
GSE18151
GSE2180
GSE74796
GSE40435
GSE11220
GSE7930
GSE46356
GSE12795
GSE6864
GSE109829
GSE81496
GSE43346
GSE14024
GSE30305
GSE42917
GSE66461
GSE51883
GSE40740
GSE43455
GSE39191
GSE52319
GSE34822
GSE104279
GSE41129
GSE85871
GSE8018
GSE82597
GSE42703
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
worki

(64, 1024)
(64, 50159)
GSE59609
GSE23261
GSE28509
GSE44551
GSE77558
GSE85681
GSE65076
GSE95012
GSE91952
GSE43114
GSE60221
GSE10702
GSE23887
GSE72071
GSE2684
GSE50591
GSE106017
GSE77778
GSE55501
GSE21717
GSE35678
GSE9776
GSE68504
GSE33141
GSE39725
GSE44805
GSE3838
GSE76830
GSE22862
GSE53983
GSE22558
GSE7156
GSE36912
GSE7463
GSE43117
GSE79797
GSE57997
GSE53147
GSE59554
GSE3784
GSE95960
GSE21696
GSE24488
GSE58593
GSE29228
GSE72809
GSE98270
GSE58194
GSE95785
GSE20087
GSE81520
GSE77366
GSE5255
GSE62748
GSE3968
GSE107218
GSE101696
GSE54899
GSE74598
GSE61916
GSE72530
GSE60107
GSE83756
GSE3418
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working

(64, 1024)
(64, 50159)
GSE5208
GSE94041
GSE32120
GSE70865
GSE94883
GSE64912
GSE76114
GSE78089
GSE55143
GSE40259
GSE47224
GSE68359
GSE22324
GSE96396
GSE34578
GSE105822
GSE46300
GSE55347
GSE32356
GSE42199
GSE43965
GSE97847
GSE40341
GSE2151
GSE31429
GSE96150
GSE99403
GSE20210
GSE6596
GSE99466
GSE12912
GSE13978
GSE20563
GSE68984
GSE65176
GSE47379
GSE98772
GSE86597
GSE84012
GSE76178
GSE18536
GSE90363
GSE65816
GSE16419
GSE103146
GSE24613
GSE32901
GSE71176
GSE70870
GSE68436
GSE4171
GSE88356
GSE33224
GSE14237
GSE92039
GSE38890
GSE15728
GSE30069
GSE3478
GSE87223
GSE95755
GSE82442
GSE73945
GSE39473
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
work

...

(64, 1024)
(64, 50159)
GSE22279
GSE65180
GSE41641
GSE35885
GSE64488
GSE62986
GSE73385
GSE673
GSE26299
GSE18304
GSE9865
GSE42000
GSE50550
GSE13928
GSE72696
GSE4965
GSE42619
GSE29500
GSE39832
GSE2044
GSE62203
GSE92807
GSE89245
GSE73553
GSE21839
GSE101633
GSE69326
GSE42748
GSE30342
GSE42694
GSE75930
GSE71461
GSE41533
GSE35240
GSE61251
GSE92806
GSE70237
GSE22048
GSE4575
GSE30136
GSE39175
GSE9882
GSE56060
GSE106157
GSE23220
GSE79254
GSE50794
GSE5675
GSE88956
GSE105582
GSE81860
GSE61878
GSE37043
GSE36240
GSE69797
GSE68981
GSE63783
GSE20172
GSE68879
GSE15074
GSE56881
GSE65213
GSE32693
GSE88542
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
workin

(64, 1024)
(64, 50159)
GSE95744
GSE16073
GSE31129
GSE20402
GSE76675
GSE24691
GSE41147
GSE86469
GSE68925
GSE90954
GSE68989
GSE52003
GSE30622
GSE34141
GSE43319
GSE85869
GSE60226
GSE20490
GSE93813
GSE45303
GSE44854
GSE29531
GSE21566
GSE35407
GSE46497
GSE42474
GSE37158
GSE88641
GSE62211
GSE88509
GSE9946
GSE77321
GSE44879
GSE93412
GSE33403
GSE15070
GSE26477
GSE13706
GSE41267
GSE15798
GSE70660
GSE45212
GSE102577
GSE24759
GSE76842
GSE10783
GSE63779
GSE77864
GSE105209
GSE45831
GSE26099
GSE101243
GSE50172
GSE785
GSE85534
GSE82844
GSE89972
GSE33072
GSE98242
GSE109955
GSE86678
GSE62548
GSE84220
GSE93987
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working


(64, 1024)
(64, 50159)
GSE65572
GSE36901
GSE98262
GSE40676
GSE27331
GSE3642
GSE26862
GSE28886
GSE4275
GSE90639
GSE26054
GSE36709
GSE20434
GSE114204
GSE43495
GSE81668
GSE103367
GSE21638
GSE85776
GSE17987
GSE24966
GSE84232
GSE88306
GSE43520
GSE12379
GSE50183
GSE100823
GSE33466
GSE35781
GSE105671
GSE46044
GSE24457
GSE11724
GSE74547
GSE28728
GSE98431
GSE5976
GSE35821
GSE11039
GSE17405
GSE91734
GSE57630
GSE25557
GSE101142
GSE42167
GSE18452
GSE24393
GSE41903
GSE34442
GSE76654
GSE11698
GSE61245
GSE36849
GSE5211
GSE41219
GSE14969
GSE56292
GSE70109
GSE10162
GSE82171
GSE24593
GSE52135
GSE30590
GSE23041
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working


(64, 1024)
(64, 50159)
GSE69672
GSE55183
GSE19236
GSE72914
GSE88529
GSE66005
GSE61105
GSE41475
GSE80953
GSE9095
GSE28026
GSE29785
GSE52538
GSE103666
GSE16348
GSE27194
GSE70019
GSE73417
GSE67710
GSE59283
GSE88098
GSE52993
GSE94568
GSE66128
GSE43821
GSE64472
GSE9559
GSE11978
GSE31215
GSE87591
GSE41770
GSE19623
GSE32273
GSE89987
GSE89711
GSE84555
GSE46297
GSE85648
GSE69786
GSE76047
GSE32028
GSE80482
GSE87463
GSE51767
GSE82603
GSE48338
GSE58763
GSE6571
GSE36943
GSE1847
GSE32931
GSE21548
GSE89422
GSE43064
GSE48791
GSE73857
GSE82739
GSE39075
GSE19106
GSE71627
GSE73105
GSE17874
GSE88230
GSE55446
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
work

(64, 1024)
(64, 50159)
GSE75463
GSE75300
GSE99535
GSE95315
GSE5285
GSE88157
GSE32283
GSE80873
GSE82703
GSE40021
GSE85687
GSE88719
GSE75876
GSE35596
GSE90333
GSE57204
GSE105649
GSE51193
GSE13371
GSE54670
GSE84090
GSE71871
GSE54438
GSE66721
GSE25399
GSE51422
GSE43110
GSE35447
GSE12615
GSE86791
GSE4749
GSE68636
GSE103272
GSE54999
GSE3956
GSE93632
GSE92229
GSE62613
GSE3290
GSE41704
GSE27568
GSE27237
GSE41636
GSE10636
GSE9490
GSE23055
GSE52445
GSE12071
GSE60120
GSE57292
GSE25860
GSE80304
GSE45887
GSE76863
GSE39128
GSE63058
GSE80022
GSE87578
GSE81094
GSE59831
GSE47872
GSE56278
GSE89816
GSE65878
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
work

In [26]:
print(step) #3371

1137


In [27]:
new_similarity_dict =  {}

for i in range(step +1):
    with open(res_addr + "new_similarity_dict_batch_" + str(i), 'rb') as fp:
        dict_batch = pickle.load(fp)
        new_similarity_dict.update(dict_batch)

with open(res_addr + 'new_similarity_dict.pickle', 'wb') as handle:
    pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [28]:
#MRR 
print('MRR:')
print(Metrics(citation_data).calculate_mrr(new_similarity_dict)) #mrr
#recall @1 and recall @10
print('recall@1, recall@10:')
print(Metrics(citation_data).calculate_recall_at_k(new_similarity_dict, 1))
print(Metrics(citation_data).calculate_recall_at_k(new_similarity_dict, 10))
#Precision@1 and precision10
print('precision@1, precision@10:')
print(Metrics(citation_data).calculate_precision_at_k(new_similarity_dict, 1))        
print(Metrics(citation_data).calculate_precision_at_k(new_similarity_dict, 10))
#MAP@10
print(Metrics(citation_data).calculate_MAP_at_k(new_similarity_dict))

MRR:
0.364137698647116
recall@1, recall@10:
0.3407533211523403
0.3995378320579925
precision@1, precision@10:
0.3464164525834238
0.040734431454438044
0.3639356361210711
